## Import libraries

In [1]:
import ee
import geemap

## Create an interactive map

In [2]:
Map = geemap.Map(center=[40, -100], zoom=4)

## Add Earth Engine Python script

In [3]:
# Add Earth Engine dataset
image = ee.Image("USGS/SRTMGL1_003")

#  ~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
#  Chapter:      F5.1 Raster/Vector Conversions
#  Checkpoint:   F51c
#  Authors:      Keiko Nomura, Samuel Bowers
#  ~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~

#-------------#
# Section 1.4 #
#-------------#

# Load required datasets.
gfc = ee.Image('UMD/hansen/global_forest_change_2020_v1_8')
wdpa = ee.FeatureCollection('WCMC/WDPA/current/polygons')

# Display deforestation.
deforestation = gfc.select('lossyear')

Map.addLayer(deforestation, {
    'min': 1,
    'max': 20,
    'palette': ['yellow', 'orange', 'red']
}, 'Deforestation raster')

# Select protected areas in the Colombian Amazon.
amazonianProtectedAreas = [
'Cordillera de los Picachos', 'La Paya', 'Nukak',
'Serrania de Chiribiquete',
'Sierra de la Macarena', 'Tinigua'
]

wdpaSubset = wdpa.filter(ee.Filter.inList('NAME',
amazonianProtectedAreas))

# Display protected areas as an outline.
protectedAreasOutline = ee.Image().byte().paint(
featureCollection = wdpaSubset,
color = 1,
width = 1
)

Map.addLayer(protectedAreasOutline, {
    'palette': 'white'
}, 'Amazonian protected areas')

# Set up map display.
Map.centerObject(wdpaSubset)
Map.setOptions('SATELLITE')

scale = deforestation.projection().nominalScale()

# Use 'reduceRegions' to sum together pixel areas in each protected area.
wdpaSubset = deforestation.gte(1) \
.multiply(ee.Image.pixelArea().divide(10000)).reduceRegions(
collection = wdpaSubset,
reducer = ee.Reducer.sum().setOutputs([
'deforestation_area']),
scale = scale
)

print(wdpaSubset.getInfo())

# Normalize by area.

def func_zfn(feat):
    return feat.set('deforestation_rate',
    ee.Number(feat.get('deforestation_area')) \
    .divide(feat.area().divide(10000)) \
    .divide(20) \
    .multiply(100)); 

wdpaSubset = wdpaSubset.map(
func_zfn)







# Print to identify rates of change per protected area.
# Which has the fastest rate of loss?
print(wdpaSubset.reduceColumns(
reducer = ee.Reducer.toList().repeat(2),
selectors = ['NAME', 'deforestation_rate']
))

#  -----------------------------------------------------------------------
#  CHECKPOINT
#  -----------------------------------------------------------------------

{'type': 'FeatureCollection', 'columns': {'CONS_OBJ': 'String', 'DESIG': 'String', 'DESIG_ENG': 'String', 'DESIG_TYPE': 'String', 'GIS_AREA': 'Float', 'GIS_M_AREA': 'Float', 'GOV_TYPE': 'String', 'INT_CRIT': 'String', 'ISO3': 'String', 'IUCN_CAT': 'String', 'MANG_AUTH': 'String', 'MANG_PLAN': 'String', 'MARINE': 'String', 'METADATAID': 'Integer', 'NAME': 'String', 'NO_TAKE': 'String', 'NO_TK_AREA': 'Float', 'ORIG_NAME': 'String', 'OWN_TYPE': 'String', 'PARENT_ISO': 'String', 'PA_DEF': 'String', 'REP_AREA': 'Float', 'REP_M_AREA': 'Float', 'STATUS': 'String', 'STATUS_YR': 'Integer', 'SUB_LOC': 'String', 'SUPP_INFO': 'String', 'VERIF': 'String', 'WDPAID': 'Float', 'WDPA_PID': 'String', 'deforestation_area': 'Float', 'system:index': 'String'}, 'features': [{'type': 'Feature', 'geometry': {'type': 'Polygon', 'coordinates': [[[-74.18315690422179, 3.1365450627443163], [-74.18308998866596, 3.1362552012866574], [-74.18297407330854, 3.1358628199149585], [-74.18284472100028, 3.135390183122738], [

## Display the interactive map

In [4]:
Map

Map(center=[1.5763278961124079, -73.22936634586408], controls=(WidgetControl(options=['position', 'transparent…